In [1]:
import pandas as pd
import numpy as np
from datetime import datetime, timedelta

### Generate random data

In [36]:
def generate_interest_rate_data(start_datetime, duration_seconds):
    # Create a range of timestamps at 1-second intervals for the specified duration
    timestamps = pd.date_range(start=start_datetime, periods=duration_seconds, freq='S')
    # Generate random interest rate levels for each timestamp
    interest_rates = np.random.uniform(0, 10, size=len(timestamps))
    # Create the DataFrame
    df = pd.DataFrame({'Datetime': timestamps, 'Interest Rate': interest_rates})
    return df

In [37]:
start_datetime = pd.Timestamp('2018-10-17 15:56:00+11:00')
duration_seconds = 3600

# Generate the DataFrame
df = generate_interest_rate_data(start_datetime, duration_seconds)

# Display the DataFrame
df.head()

Datetime  Interest Rate
0 2018-10-17 15:56:00+11:00       2.848223
1 2018-10-17 15:56:01+11:00       9.386088
2 2018-10-17 15:56:02+11:00       6.992151
3 2018-10-17 15:56:03+11:00       4.588865
4 2018-10-17 15:56:04+11:00       3.618940

In [14]:
df.dtypes

Datetime         datetime64[ns, pytz.FixedOffset(660)]
Interest Rate                                  float64
dtype: object

### Compute_realized_volatility function
#### For a 5min realized vol (on 1 datapoint each second)

In [11]:
def compute_realized_volatility(data, window_minutes):
    # Compute the number of periods based on the window size
    window_periods = int(window_minutes * 60)
    # Calculate the difference between interest rates
    data['Rate Difference'] = data['Interest Rate'].diff()  
    # Calculate the squared differences
    data['Squared Difference'] = data['Rate Difference']**2
    # Compute the rolling sum of squared differences for the given window
    data['Rolling Sum'] = data['Squared Difference'].rolling(window_periods).sum()
    # Compute the realized volatility as the square root of the rolling sum
    data['Realized Volatility'] = data['Rolling Sum'].apply(lambda x: x**0.5)
    # Drop intermediate columns
    data = data.drop(['Rate Difference', 'Squared Difference', 'Rolling Sum'], axis=1)
    return data

In [12]:
# Assuming you already have the DataFrame named 'df' with datetime and interest rate columns
window_minutes = 5  # Specify the window size in minutes
# Apply the function to compute realized volatility
df = compute_realized_volatility(df, window_minutes)
# Display the updated DataFrame
# Set display options to show all rows and columns
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)
df.tail()

Datetime  Interest Rate  Realized Volatility
3595 2018-10-17 16:55:55+11:00       2.922579            70.107239
3596 2018-10-17 16:55:56+11:00       3.583283            70.052702
3597 2018-10-17 16:55:57+11:00       4.467072            69.667009
3598 2018-10-17 16:55:58+11:00       9.583878            69.846560
3599 2018-10-17 16:55:59+11:00       3.029712            70.089366

### Realized_volatility function
#### For a list of number of minutes realized vol (on 1 datapoint each second)

In [5]:
def realized_volatility(data, window_minutes_list):
    for window_minutes in window_minutes_list:
        # Compute the number of periods based on the window size
        window_periods = int(window_minutes * 60)

        # Calculate the difference between interest rates
        data['Rate Difference'] = data['Interest Rate'].diff()

        # Calculate the squared differences
        data['Squared Difference'] = data['Rate Difference']**2

        # Compute the rolling sum of squared differences for the given window
        data['Rolling Sum'] = data['Squared Difference'].rolling(window_periods).sum()

        # Compute the realized volatility as the square root of the rolling sum
        col_name = f'Realized Volatility {window_minutes}min'
        data[col_name] = data['Rolling Sum'].apply(lambda x: x**0.5)

        # Drop intermediate columns
        data = data.drop(['Rate Difference', 'Squared Difference', 'Rolling Sum'], axis=1)

    return data

In [ ]:
df.head()

In [44]:
# Assuming you already have the DataFrame named 'df' with datetime and interest rate columns
window_minutes_list = [1, 5, 15, 30, 60]  # Specify the window sizes in minutes

# Apply the function to compute realized volatility for each window size
df = realized_volatility(df, window_minutes_list)

# Display the updated DataFrame
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)
df.tail(50)

Datetime  Interest Rate  Realized Volatility 1min  \
7150 2018-10-17 17:55:10+11:00       4.731094                 30.757988   
7151 2018-10-17 17:55:11+11:00       6.148694                 30.790011   
7152 2018-10-17 17:55:12+11:00       3.815629                 30.420031   
7153 2018-10-17 17:55:13+11:00       1.222432                 30.524052   
7154 2018-10-17 17:55:14+11:00       5.438954                 30.153502   
7155 2018-10-17 17:55:15+11:00       7.753192                 30.084010   
7156 2018-10-17 17:55:16+11:00       5.715949                 29.541043   
7157 2018-10-17 17:55:17+11:00       4.384723                 29.568809   
7158 2018-10-17 17:55:18+11:00       6.286671                 29.491848   
7159 2018-10-17 17:55:19+11:00       9.415025                 28.994129   
7160 2018-10-17 17:55:20+11:00       7.444525                 27.896222   
7161 2018-10-17 17:55:21+11:00       3.194249                 27.695228   
7162 2018-10-17 17:55:22+11:00       9.400077                 28.229945   
7163 2018-10-17 17:55:23+11:00       1.916049                 29.182691   
7164 2018-10-17 17:55:24+11:00       5.894319                 29.227236   
7165 2018-10-17 17:55:25+11:00       4.642735                 29.177668   
7166 2018-10-17 17:55:26+11:00       0.500022                 29.363565   
7167 2018-10-17 17:55:27+11:00       2.259446                 29.232785   
7168 2018-10-17 17:55:28+11:00       8.885548                 29.285644   
7169 2018-10-17 17:55:29+11:00       4.529984                 29.211132   
7170 2018-10-17 17:55:30+11:00       9.917473                 28.617609   
7171 2018-10-17 17:55:31+11:00       1.171484                 28.430802   
7172 2018-10-17 17:55:32+11:00       7.897968                 28.444564   
7173 2018-10-17 17:55:33+11:00       4.262971                 28.528318   
7174 2018-10-17 17:55:34+11:00       3.406943                 28.540712   
7175 2018-10-17 17:55:35+11:00       8.078162                 28.906797   
7176 2018-10-17 17:55:36+11:00       8.989192                 28.916774   
7177 2018-10-17 17:55:37+11:00       1.105488                 29.937653   
7178 2018-10-17 17:55:38+11:00       3.498635                 29.813737   
7179 2018-10-17 17:55:39+11:00       2.616032                 29.765988   
7180 2018-10-17 17:55:40+11:00       8.370787                 30.147182   
7181 2018-10-17 17:55:41+11:00       7.529270                 29.809041   
7182 2018-10-17 17:55:42+11:00       8.439915                 29.583970   
7183 2018-10-17 17:55:43+11:00       5.617312                 29.693113   
7184 2018-10-17 17:55:44+11:00       1.782902                 29.703551   
7185 2018-10-17 17:55:45+11:00       1.779656                 29.646104   
7186 2018-10-17 17:55:46+11:00       2.330683                 29.614573   
7187 2018-10-17 17:55:47+11:00       6.199883                 29.418684   
7188 2018-10-17 17:55:48+11:00       9.373588                 29.204045   
7189 2018-10-17 17:55:49+11:00       6.095695                 29.381417   
7190 2018-10-17 17:55:50+11:00       3.022909                 29.491986   
7191 2018-10-17 17:55:51+11:00       6.262002                 29.414206   
7192 2018-10-17 17:55:52+11:00       3.719001                 29.405005   
7193 2018-10-17 17:55:53+11:00       7.517954                 28.637031   
7194 2018-10-17 17:55:54+11:00       8.031551                 28.639287   
7195 2018-10-17 17:55:55+11:00       1.376778                 29.236429   
7196 2018-10-17 17:55:56+11:00       7.158729                 29.738959   
7197 2018-10-17 17:55:57+11:00       2.507200                 29.989806   
7198 2018-10-17 17:55:58+11:00       1.384987                 30.010038   
7199 2018-10-17 17:55:59+11:00       3.937985                 29.949411   

      Realized Volatility 5min  Realized Volatility 15min  \
7150                 74.070094                 123.849799   
7151                 73.865219                 123.843101   
7152         

## Annualized Realized volatilities

#### Genereating the Data

In [42]:
start_datetime = pd.Timestamp('2018-10-17 15:56:00+11:00')
duration_seconds = 7200

# Generate the DataFrame
df = generate_interest_rate_data(start_datetime, duration_seconds)
df.head()

Datetime  Interest Rate
0 2018-10-17 15:56:00+11:00       0.842274
1 2018-10-17 15:56:01+11:00       7.692632
2 2018-10-17 15:56:02+11:00       2.566832
3 2018-10-17 15:56:03+11:00       1.627602
4 2018-10-17 15:56:04+11:00       9.591370

#### Defining the function

In [40]:
def compute_realized_volatility(data, window_minutes_list):
    for window_minutes in window_minutes_list:
        # Compute the number of periods based on the window size
        window_periods = int(window_minutes * 60)

        # Calculate the difference between interest rates
        data['Rate Difference'] = data['Interest Rate'].diff()

        # Calculate the squared differences
        data['Squared Difference'] = data['Rate Difference']**2

        # Compute the rolling sum of squared differences for the given window
        data['Rolling Sum'] = data['Squared Difference'].rolling(window_periods).sum()

        # Compute the realized volatility as the square root of the rolling sum
        col_name = f'Realized Volatility {window_minutes}min'
        data[col_name] = data['Rolling Sum'].apply(lambda x: x**0.5)

        # Drop intermediate columns
        data = data.drop(['Rate Difference', 'Squared Difference', 'Rolling Sum'], axis=1)

    return data

In [43]:
# Assuming you already have the DataFrame named 'df' with datetime and interest rate columns
window_minutes_list = [1, 5, 15, 30, 60]  # Specify the window sizes in minutes

# Apply the function to compute annualized realized volatility for each window size
df = compute_realized_volatility(df, window_minutes_list)

# Display the updated DataFrame
df

Datetime  Interest Rate  Realized Volatility 1min  \
0    2018-10-17 15:56:00+11:00       0.842274                       NaN   
1    2018-10-17 15:56:01+11:00       7.692632                       NaN   
2    2018-10-17 15:56:02+11:00       2.566832                       NaN   
3    2018-10-17 15:56:03+11:00       1.627602                       NaN   
4    2018-10-17 15:56:04+11:00       9.591370                       NaN   
5    2018-10-17 15:56:05+11:00       1.487358                       NaN   
6    2018-10-17 15:56:06+11:00       6.469440                       NaN   
7    2018-10-17 15:56:07+11:00       1.542106                       NaN   
8    2018-10-17 15:56:08+11:00       9.370645                       NaN   
9    2018-10-17 15:56:09+11:00       9.396712                       NaN   
10   2018-10-17 15:56:10+11:00       9.570405                       NaN   
11   2018-10-17 15:56:11+11:00       7.197155                       NaN   
12   2018-10-17 15:56:12+11:00       0.152437                       NaN   
13   2018-10-17 15:56:13+11:00       3.201357                       NaN   
14   2018-10-17 15:56:14+11:00       8.764236                       NaN   
15   2018-10-17 15:56:15+11:00       0.688073                       NaN   
16   2018-10-17 15:56:16+11:00       1.265330                       NaN   
17   2018-10-17 15:56:17+11:00       5.878863                       NaN   
18   2018-10-17 15:56:18+11:00       6.961594                       NaN   
19   2018-10-17 15:56:19+11:00       6.015599                       NaN   
20   2018-10-17 15:56:20+11:00       6.742649                       NaN   
21   2018-10-17 15:56:21+11:00       0.542754                       NaN   
22   2018-10-17 15:56:22+11:00       6.932149                       NaN   
23   2018-10-17 15:56:23+11:00       6.031198                       NaN   
24   2018-10-17 15:56:24+11:00       0.175270                       NaN   
25   2018-10-17 15:56:25+11:00       5.050814                       NaN   
26   2018-10-17 15:56:26+11:00       2.336853                       NaN   
27   2018-10-17 15:56:27+11:00       9.345523                       NaN   
28   2018-10-17 15:56:28+11:00       0.168101                       NaN   
29   2018-10-17 15:56:29+11:00       7.980820                       NaN   
30   2018-10-17 15:56:30+11:00       9.591736                       NaN   
31   2018-10-17 15:56:31+11:00       7.355196                       NaN   
32   2018-10-17 15:56:32+11:00       8.547007                       NaN   
33   2018-10-17 15:56:33+11:00       6.993853                       NaN   
34   2018-10-17 15:56:34+11:00       5.075931                       NaN   
35   2018-10-17 15:56:35+11:00       3.680985                       NaN   
36   2018-10-17 15:56:36+11:00       9.728184                       NaN   
37   2018-10-17 15:56:37+11:00       3.020767                       NaN   
38   2018-10-17 15:56:38+11:00       5.716033                       NaN   
39   2018-10-17 15:56:39+11:00       9.581512                       NaN   
40   2018-10-17 15:56:40+11:00       6.763745                       NaN   
41   2018-10-17 15:56:41+11:00       4.036889                       NaN   
42   2018-10-17 15:56:42+11:00       2.770417                       NaN   
43   2018-10-17 15:56:43+11:00       2.519319                       NaN   
44   2018-10-17 15:56:44+11:00       0.126681                       NaN   
45   2018-10-17 15:56:45+11:00       3.078653                       NaN   
46   2018-10-17 15:56:46+11:00       0.417492                       NaN   
47   2018-10-17 15:56:47+11:00       3.676923                       NaN   
48   2018-10-17 15:56:48+11:00       2.460903                       NaN   
49   2018-10-17 15:56:49+11:00       3.303107                       NaN   
50   2018-10-17 15:56:50+11:00       8.230996                       NaN   
51   2018-10-17 15:56:51+11:00       3.721995                       NaN   
52   2018-10-17 15:56:52+11:00       8.001772  